# Introduction to Stable Diffusion Using Google Colab Workshop
Jim Plaxco, www.artsnova.com


---

#SECTION 1: STABLE DIFFUSION

---


**Step 1**: Make sure that the runtime type is GPU 
        ( Runtime -> Change Runtime type -> Hardware Accelerator =  GPU )
        Click Save after selecting GPU
Verify GPU availability

Documentation for the nvidia command is at https://developer.nvidia.com/nvidia-system-management-interface

In [ ]:
!nvidia-smi

**Step 2**: Install the various libraries. Note that some libraries may already be installed

In [ ]:
# install the libraries using pip3 (Package Installer for Python 3)
# NOTE: accelerate is not required but speeds up the inference process a lot 
!pip3 install diffusers transformers scipy ftfy accelerate


**Step 3**: Once libraries are installed, Import the various libraries.

In [ ]:
#  import the various libraries needed by Stable Diffusion
from diffusers import StableDiffusionPipeline, EulerDiscreteScheduler, DiffusionPipeline, DPMSolverMultistepScheduler
import torch

# the following libraries are used to output the image to the screen
from PIL import Image
from IPython.display import display

**Step 4**: Import the Hugginface interface so you can enter your Stable Diffusion API key (token) using the notebook_login() function


In [ ]:
#@title Login
# have your Huggingface API key (token) ready
from huggingface_hub import notebook_login
notebook_login()


**Step 5**: Set up the processing pipeline. And while we are at it, disable the NSFW (Not Safe For Work) filter. 

Note that if Stable Diffusion thinks the output image may be NSFW, you will get an all black image as output. 

In [ ]:
# create the  pipeline (this pipeline is made with Euler Scheduler):
model_id = "mann-e/mann-e_rev-3"

scheduler = EulerDiscreteScheduler.from_pretrained(model_id, subfolder="scheduler")

pipe = StableDiffusionPipeline.from_pretrained(model_id, scheduler=scheduler, torch_dtype=torch.float16)
# use GPU
pipe = pipe.to("cuda")

# disable NSFW filter 
# the following code is optional and may be deleted
def nonsfw(images, **kwargs): 
    return images, False 

pipe.safety_checker = nonsfw


**Step 6:** Generate Images.
This section will be run each time we want to create a new image. It is the only code block that you will run more than once.

**Google Colab Parameters**
#@param is a parameter for the Colab GUI that allows you to set variable values using the Colab GUI instead of inserting them directly into the code.

**Stable Diffusion Parameters**

**prompt**: This is the text prompt that describes what you want your image to look like

**negative_prompt**: This is what you do not want to see in your image

**inference_steps**: The number of steps of processing. This value impacts how long it will take to generate an image. A good starting value is 50

**guidance**: How strictly or losely do you want your words to be interpreted. A good starting value is 7.5 


In [ ]:
# start the image generation process
# Set your parameters
prompt = "vintage rocket flying in space, concept art, centered, hdr render" #@param {type:"string"}
negative_prompt = "low quality, blurry"  #@param {type:"string"}
inference_steps = 28  #@param {type:"slider", min:0, max:240, step:1}
guidance = 7.0    #@param {type:"slider", min:0, max:20, step:0.1}
width = 768      # width in pixels must be a multiple of 256
height = 512     # height in pixels must be a multiple of 256

# Generate the image
image = pipe(prompt=prompt, 
             negative_prompt=negative_prompt, 
             num_inference_steps=inference_steps, 
             width=width, height=height, 
             guidance_scale=guidance).images[0]
#image.save("My_image.png")
filename = prompt.replace(",","") + "-Steps"+str(inference_steps) + "-guide"+str(guidance)+".png"
filenameout = filename.replace(" ", "_" )
print(filenameout)
image


---
A SECOND VERSION OF THE CODE IN STEP 6 EXECPT IT PRINTS OUT A FILENAME THAT CAN BE USED WHEN SAVING A FILE. 

---



In [ ]:
# start the image generation process
# Set your parameters
prompt = "waterfall with swirling water in a shallow wide stream, hdr, colorful, detailed" #@param {type:"string"}
negative_prompt = "low quality, blurry"  #@param {type:"string"}
inference_steps = 8 #@param {type:"slider", min:0, max:240, step:1}
guidance = 2.3  #@param {type:"slider", min:0, max:20, step:0.1}
width = 768 
height = 512 

# Generate the image
image = pipe(prompt=prompt, 
             negative_prompt=negative_prompt, 
             num_inference_steps=inference_steps, 
             width=width, height=height, 
             guidance_scale=guidance).images[0]
#image.save("My_image.png")
filename = prompt + "-"+str(inference_steps) + "-"+str(guidance)
print(filename)
image

Step 7: One way to generate multiple images is to pass a list into the pipeline. This requires more VRAM.


In [ ]:
# start the image generation process
# Set your parameters
quantity = 3 #@param {type:"integer"}
prompt = "moon in sky polychrome woodblock print" #@param {type:"string"}
negative_prompt = "low quality, blurry"  #@param {type:"string"}
inference_steps = 50 #@param {type:"slider", min:0, max:240, step:1}
guidance = 5.3  #@param {type:"slider", min:0, max:20, step:0.1}
width = 512
height = 512 

# Generate the image
promptlist = [prompt] * quantity
negpromptlist = [negative_prompt] * quantity
# image is a Python list with one element for each image
image = pipe(prompt=promptlist, 
             negative_prompt=negpromptlist, 
             num_inference_steps=inference_steps, 
             width=width, height=height, 
             guidance_scale=guidance).images

for img in image:
  display(img)
  print("-----")


Step 8: A second way to generate multiple images is to invoke the pipeline once per image count. 

In [ ]:
# start the image generation process
# Set your parameters
quantity = 4 #@param {type:"integer"}
prompt = "rocketship in orbit around moon, 1950s, detailed  panoramic illustration" #@param {type:"string"}
negative_prompt = "low quality, blurry, words"  #@param {type:"string"}
inference_steps = 36 #@param {type:"slider", min:0, max:240, step:1}
guidance = 6  #@param {type:"slider", min:0, max:20, step:0.1}
width = 1024
height = 768

filename = prompt.replace(",","") + "-Steps"+str(inference_steps) + "-guide"+str(guidance)+"-1.png"
filenameout = filename.replace(" ", "_" )
print(filenameout)

for indx in range(0, quantity):
    # Generate the image
    image = pipe(prompt=prompt, 
             negative_prompt=negative_prompt, 
             num_inference_steps=inference_steps, 
             width=width, height=height, 
             guidance_scale=guidance).images[0]
    #image.save("My_image.png")
    display(image)
# done

# **The End**

NOTE: If at some point your pipeline abends, you should run the following code to reclaim allocated memory

In [ ]:
### USE THIS TO FREE MEMORY AFTER AN OUTOFMEMORYERROR ERROR OR AN ABEND
import gc
torch.cuda.empty_cache()
gc.collect()